In [100]:
#Import Libraries
import openai
import langchain
#import pinecone
from langchain.document_loaders import PyPDFDirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.embeddings.openai import OpenAIEmbeddings

from langchain.llms import OpenAI


In [89]:
from dotenv import load_dotenv
load_dotenv()

True

In [104]:
import os

In [91]:
#Lets read the document
def read_doc(directory):
    file_loader=PyPDFDirectoryLoader(directory)
    documents=file_loader.load()
    return documents

In [92]:
doc=read_doc('documents/')
len(doc)

61

In [93]:
#Divide the docs into chuncks
def chunk_data(docs,chunk_size=800,chunk_overlap=50):
    text_splitter=RecursiveCharacterTextSplitter(chunk_size=chunk_size,chunk_overlap=chunk_overlap)
    docs=text_splitter.split_documents(docs)
    return docs
    

In [94]:
documents=chunk_data(docs=doc)
len(documents)


187

In [ ]:
#Embedding Technique of OPENAI
embeddings=OpenAIEmbeddings(api_key=os.environ['OPENAI_API_KEY'])
embeddings

In [96]:
vectors=embeddings.embed_query("How are you?")
len(vectors)

1536

In [106]:
from pinecone import Pinecone, ServerlessSpec
os.environ['PINECONE_API_KEY'] = "870db653-5972-4c49-a639-6f497a3660dc"
pc = Pinecone(api_key=os.environ['PINECONE_API_KEY'])

In [107]:
import time

index_name = "langchainvector"  # change if desired

existing_indexes = [index_info["name"] for index_info in pc.list_indexes()]

if index_name not in existing_indexes:
    pc.create_index(
        name=index_name,
        dimension=1536,
        metric="cosine",
        spec=ServerlessSpec(cloud="aws", region="us-east-1"),
    )
    while not pc.describe_index(index_name).status["ready"]:
        time.sleep(1)

index = pc.Index(index_name)

In [108]:
from langchain_pinecone import PineconeVectorStore

docsearch = PineconeVectorStore.from_documents(documents, embeddings, index_name=index_name)

In [121]:
#Similarity Retrieve Result
def retrieve_query(query,k=2):
    matching_results=docsearch.similarity_search(query,k=k)
    return matching_results
    

In [122]:
from langchain.chains.question_answering import load_qa_chain
from langchain import OpenAI
llm=OpenAI(model_name="gpt-3.5-turbo-instruct",temperature=0.5)
chain=load_qa_chain(llm,chain_type="stuff")

c:\Users\Matt Brown\AppData\Local\Programs\Python\Python312\Lib\site-packages\langchain_core\_api\deprecation.py:139: LangChainDeprecationWarning: The class `OpenAI` was deprecated in LangChain 0.0.10 and will be removed in 0.3.0. An updated version of the class exists in the langchain-openai package and should be used instead. To use it run `pip install -U langchain-openai` and import as `from langchain_openai import OpenAI`.
  warn_deprecated(


In [123]:
def retrieve_answers(query):
    doc_search=retrieve_query(query)
    print(doc_search)
    response=chain.run(input_documents=doc_search,question=query)  
    return response  

In [ ]:
query = "What are indirect emissions?"
answer=retrieve_answers(query)
print(answer)

In [ ]:
query = "What are scope 2 emissions?"
docs = docsearch.similarity_search(query,k=2)
print(docs[0].page_content)

In [ ]:
retriever = docsearch.as_retriever(search_type="mmr")
matched_docs = retriever.invoke(query)
for i, d in enumerate(matched_docs):
    print(f"\n## Document {i}\n")
    print(d.page_content)

In [ ]:
found_docs = docsearch.max_marginal_relevance_search(query, k=2, fetch_k=10)
for i, doc in enumerate(found_docs):
    print(f"{i + 1}.", doc.page_content, "\n")